In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()
sns.set_style("whitegrid")
sns.set_palette("GnBu_d")
import folium
from folium import plugins
from folium.plugins import HeatMap
from datetime import datetime
from datetime import timedelta
import math
import random 
import timeit

In [2]:
#jupyter trust density.ipynb
#jupyter notebook notebook-name.ipynb

In [3]:
brm = pd.read_csv("../resources/bremen.csv")
frb = pd.read_csv("../resources/freiburg.csv")

In [4]:
#create an additional column, which will later be needed for the hourlty differentiation 
brm["weight"]=brm["time"].map(lambda x:int(x[0:2]))
frb["weight"]=frb["time"].map(lambda x:int(x[0:2]))
frb.head(3)

day      time  b_number      city              trip_duration  \
0  2019-05-06  14:22:00     32560  freiburg  0 days 00:07:00.000000000   
1  2019-05-07  10:42:00     32560  freiburg  0 days 00:07:00.000000000   
2  2019-05-07  11:02:00     32560  freiburg  0 days 00:09:00.000000000   

    orig_lat  orig_lng   dest_lat  dest_lng  weight  
0  47.993178  7.795708  47.994027  7.796084      14  
1  47.994191  7.796853  47.991960  7.797405      10  
2  47.992044  7.797352  47.992000  7.797478      11

In [5]:
brm["day"].max()


'2020-01-20'

In [6]:
#split the datasets of the two cities into 4 smaller datasets respectively for the 4 seasons
frb_spring =  frb[(frb['day'] >= "2019-03-01") & (frb['day'] <= "2019-05-31")]
frb_summer =  frb[(frb['day'] >= "2019-06-01") & (frb['day'] <= "2019-09-31")] 
frb_fall   =  frb[(frb['day'] >= "2019-09-01") & (frb['day'] <= "2019-11-30")]
frb_winter =  frb[(frb['day'] >= "2019-12-01") & (frb['day'] <= "2020-01-20")]

brm_spring =  brm[(brm['day'] >= "2019-03-01") & (brm['day'] <= "2019-05-31")]
brm_summer =  brm[(brm['day'] >= "2019-06-01") & (brm['day'] <= "2019-09-31")] 
brm_fall   =  brm[(brm['day'] >= "2019-09-01") & (brm['day'] <= "2019-11-30")]
brm_winter =  brm[(brm['day'] >= "2019-12-01") & (brm['day'] <= "2020-01-20")]

In [7]:
brm_winter

day      time  b_number    city              trip_duration  \
37      2019-12-07  09:16:00     20507  bremen  0 days 00:06:00.000000000   
38      2019-12-07  09:24:00     20507  bremen  0 days 00:06:00.000000000   
39      2019-12-19  15:49:00     20507  bremen  0 days 02:03:00.000000000   
40      2019-12-20  17:16:00     20507  bremen  0 days 00:33:00.000000000   
41      2019-12-20  17:57:00     20507  bremen  0 days 00:12:00.000000000   
...            ...       ...       ...     ...                        ...   
156696  2019-12-22  12:32:00     20996  bremen  0 days 00:21:00.000000000   
157410  2019-12-06  18:07:00     20998  bremen  0 days 00:16:00.000000000   
157411  2019-12-07  04:50:00     20998  bremen  0 days 00:18:00.000000000   
157412  2019-12-08  00:10:00     20998  bremen  0 days 00:21:00.000000000   
157413  2019-12-15  03:22:00     20998  bremen  0 days 00:33:00.000000000   

         orig_lat  orig_lng   dest_lat  dest_lng  weight  
37      53.078923  8.884911  53.081427  8.893282       9  
38      53.081529  8.893232  53.078923  8.884911       9  
39      53.076440  8.889202  53.078923  8.884911      15  
40      53.078923  8.884911  53.077538  8.911175      17  
41      53.077458  8.910761  53.078923  8.884911      17  
...           ...       ...        ...       ...     ...  
156696  53.096787  8.785236  53.069524  8.791103      12  
157410  53.097333  8.812972  53.078684  8.800971      18  
157411  53.078880  8.800464  53.073316  8.794113       4  
157412  53.073493  8.794131  53.097662  8.805812       0  
157413  53.097591  8.805994  53.078271  8.772927       3  

[19122 rows x 10 columns]

In [8]:
# Ensure we are handing it floats
frb['orig_lat'] = frb['orig_lat'].astype(float)
frb['orig_lng'] = frb['orig_lng'].astype(float)

brm['orig_lat'] = brm['orig_lat'].astype(float)
brm['orig_lng'] = brm['orig_lng'].astype(float)

In [9]:
#create the empty map of the city
frb_map_summer = folium.Map(location = [48.3669, 7.1485],
                          tiles ='Stamen Toner',
                           zoom_start = 13) 

#create a list of lists with the latitude, longitude and the tiem as weight 
frb_heat_data_summer = [[[row['orig_lat'],row['orig_lng']] for index,
              row in frb_summer[frb_summer['weight'] == i].iterrows()]
             for i in range(0,23)]

# Plot it on the map
frb_hm_sm = plugins.HeatMapWithTime(frb_heat_data_summer,auto_play=False,max_opacity=0.8)
frb_hm_sm.add_to(frb_map_summer)

# Display the map
frb_map_summer



In [10]:
#create the empty map of the city
frb_map_winter = folium.Map(location = [48.3669, 7.1485],
                          tiles ='Stamen Toner',
                           zoom_start = 13) 

#create a list of lists with the latitude, longitude and the tiem as weight 
frb_heat_data_winter = [[[row['orig_lat'],row['orig_lng']] for index,
              row in frb_winter[frb_winter['weight'] == i].iterrows()]
             for i in range(0,23)]

#plot it on the map
frb_hm_wi = plugins.HeatMapWithTime(frb_heat_data_winter,auto_play=False,max_opacity=0.8)
frb_hm_wi.add_to(frb_map_winter)

#display the map
frb_map_winter



In [11]:
#create the empty map of the city
brm_map_summer = folium.Map(location = [53.8299, 7.7985],
                          tiles ='Stamen Toner',
                           zoom_start = 13) 

#create a list of lists with the latitude, longitude and the tiem as weight 
brm_heat_data_summer = [[[row['orig_lat'],row['orig_lng']] for index,
              row in brm_summer[brm_summer['weight'] == i].iterrows()]
             for i in range(0,23)]

#plot it on the map
brm_hm_sm = plugins.HeatMapWithTime(brm_heat_data_summer,auto_play=False,max_opacity=0.8)
brm_hm_sm.add_to(brm_map_summer)

#display the map
brm_map_summer



In [12]:
#create the empty map of the city
brm_map_winter = folium.Map(location = [53.8299, 7.7985],
                          tiles ='Stamen Toner',
                           zoom_start = 13) 

#create a list of lists with the latitude, longitude and the tiem as weight 
brm_heat_data_winter = [[[row['orig_lat'],row['orig_lng']] for index,
              row in brm_winter[brm_winter['weight'] == i].iterrows()]
             for i in range(0,23)]

# Plot it on the map
brm_hm_wi = plugins.HeatMapWithTime(brm_heat_data_winter,auto_play=False,max_opacity=0.8)
brm_hm_wi.add_to(brm_map_winter)

# Display the map
brm_map_winter

 -Calculate hourly KPIs for the two cities in your dataset and visualize them over time. 
 -Which trends do you observe?
 -How do you explain them? 
 –Find explanations for any diﬀerences between cities. Which city performs better/worse and why? 
    
    The density-KPI is more or less mirroring the commuting patterns of our clients. In the morning interval (7:00 - 10:00) there is a clear movement from the populated outskirt towards the city-center. An assumption can be made that this is due to the large number of people traveling to work or school. 
    In the middle of the day (12:00 - 14:00) the activity is concentrated in the city area. We can interpret that as people running errands in their lunch breaks or in general.
    The last clear observation takes place in the time period from around 17:00 until the end of the day and it shows the traffic leading out of the city.
    By taking the small hours of the morning into consideration, which are leading to the initial statement made about the morning-commutes, this closes a full circle.
    
    
    

In [13]:
len(brm["b_number"].unique())

441

In [14]:
len(frb["b_number"].unique())

435